In [1]:
!git clone https://github.com/ultralytics/yolov5  # clone

Cloning into 'yolov5'...
remote: Enumerating objects: 16965, done.
remote: Counting objects: 100% (160/160), done.
remote: Compressing objects: 100% (110/110), done.
remote: Total 16965 (delta 79), reused 102 (delta 50), pack-reused 16805 (from 1)
Receiving objects: 100% (16965/16965), 15.71 MiB | 10.50 MiB/s, done.
Resolving deltas: 100% (11617/11617), done.


In [2]:
%cd yolov5

/home/aakash/Aakash/object_detection/yolov5


In [3]:
%pip install -qr requirements.txt  # install

Note: you may need to restart the kernel to use updated packages.


In [5]:
import torch

import utils

display = utils.notebook_init()  # checks

YOLOv5 🚀 v7.0-368-gb163ff8d Python-3.10.14 torch-2.4.1+cu121 CUDA:0 (NVIDIA GeForce RTX 3060, 12036MiB)


Setup complete ✅ (20 CPUs, 31.1 GB RAM, 423.7/937.3 GB disk)



Create the thermal_imaging_dataset.yaml file

In [ ]:
# # thermal_imaging_dataset.yaml

# train: /home/aakash/Aakash/object_detection/thermal_images/train/
# val: /home/aakash/Aakash/object_detection/thermal_images/val/
# test: /home/aakash/Aakash/object_detection/thermal_images/test/
# nc: 15  # Number of classes (update this based on the number of classes in your dataset)

# # Class names according to the modified MSCOCO label map
# names:
#   0: person
#   1: bike
#   2: car
#   3: motor
#   4: bus
#   5: train
#   6: truck
#   7: light
#   8: hydrant
#   9: sign
#   10: dog
#   11: skateboard
#   12: stroller
#   13: scooter
#   14: other vehicle

In [31]:
#Remap and Convert COCO Annotations to YOLO Format 
import os
import json

# COCO to YOLO class ID remapping (from COCO to YOLO indices)
category_id_mapping = {
    1: 0,  # person
    2: 1,  # bike
    3: 2,  # car
    4: 3,  # motor
    6: 4,  # bus
    7: 5,  # train
    8: 6,  # truck
    10: 7, # light
    11: 8, # hydrant
    12: 9, # sign
    17: 10, # dog
    37: 11, # skateboard
    73: 12, # stroller
    77: 13, # scooter
    79: 14, # other vehicle
}

# Paths
coco_json_path = "/home/aakash/Aakash/object_detection/task-4_thermal-object-detection/data/FLIR_ADAS_v2/video_thermal_test/coco_updated.json"  # Path to your coco.json file
images_dir = "/home/aakash/Aakash/object_detection/task-4_thermal-object-detection/data/FLIR_ADAS_v2/video_thermal_test/data"  # Path to the images directory
output_dir = "/home/aakash/Aakash/object_detection/task-4_thermal-object-detection/data/FLIR_ADAS_v2/video_thermal_test/labels"  # Path where YOLO label .txt files will be saved

# Create output directory if it doesn't exist
if not os.path.exists(output_dir):
    os.makedirs(output_dir)

# Load COCO JSON
with open(coco_json_path, 'r') as f:
    coco_data = json.load(f)

# Extract image info from COCO JSON
images = {img['id']: img for img in coco_data['images']}

# Process each annotation
for annotation in coco_data['annotations']:
    image_id = annotation['image_id']
    image_info = images[image_id]
    img_width = image_info['width']
    img_height = image_info['height']

    # COCO bbox format: [x_min, y_min, width, height]
    bbox = annotation['bbox']
    x_min, y_min, bbox_width, bbox_height = bbox

    # Convert to YOLO format: [x_center, y_center, bbox_width, bbox_height] (normalized)
    x_center = (x_min + bbox_width / 2) / img_width
    y_center = (y_min + bbox_height / 2) / img_height
    bbox_width /= img_width
    bbox_height /= img_height

    # Remap category_id to YOLO class id
    coco_category_id = annotation['category_id']
    if coco_category_id in category_id_mapping:
        yolo_class_id = category_id_mapping[coco_category_id]
    else:
        continue  # Skip if the category_id is not in the mapping

    # Get the image file name without extension
    image_file_name = os.path.splitext(image_info['file_name'])[0]

    # Prepare the YOLO label file path
    label_file_path = os.path.join(output_dir, f"{image_file_name}.txt")

    # Write to the YOLO label file
    with open(label_file_path, 'a') as label_file:
        label_file.write(f"{yolo_class_id} {x_center} {y_center} {bbox_width} {bbox_height}\n")

print(f"YOLO labels created in {output_dir}")


YOLO labels created in /home/aakash/Aakash/object_detection/task-4_thermal-object-detection/data/FLIR_ADAS_v2/video_thermal_test/labels


In [32]:
## Step3 All images donot have images, create empty file for the images which donot have labels
import os

# Path to your images directory
images_dir = "/home/aakash/Aakash/object_detection/task-4_thermal-object-detection/data/FLIR_ADAS_v2/video_thermal_test/data"
# Path to your labels directory
labels_dir = "/home/aakash/Aakash/object_detection/task-4_thermal-object-detection/data/FLIR_ADAS_v2/video_thermal_test/labels"

# List of all images
image_files = [f for f in os.listdir(images_dir) if f.endswith(('.jpg', '.png'))]

# List of all labels
label_files = [f.replace('.txt', '') for f in os.listdir(labels_dir) if f.endswith('.txt')]

# Create empty label files for images without corresponding labels
missing_labels = 0
for image_file in image_files:
    image_name = os.path.splitext(image_file)[0]  # Get the image name without extension
    label_file_path = os.path.join(labels_dir, f"{image_name}.txt")
    
    # Check if the label exists, if not create an empty .txt file
    if image_name not in label_files:
        with open(label_file_path, 'w') as f:
            pass  # Create an empty file
        missing_labels += 1

print(f"Created {missing_labels} empty label files for images without annotations.")

Created 256 empty label files for images without annotations.


### Train the pre-trained YOLOv5 model on the custom thermal image dataset

In [33]:
!python train.py --img 640 --batch 16 --epochs 30 --data thermal_imaging_dataset.yaml --weights yolov5s.pt

train: weights=yolov5s.pt, cfg=, data=thermal_imaging_dataset.yaml, hyp=data/hyps/hyp.scratch-low.yaml, epochs=30, batch_size=16, imgsz=640, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, noplots=False, evolve=None, evolve_population=data/hyps, resume_evolve=None, bucket=, cache=None, image_weights=False, device=, multi_scale=False, single_cls=False, optimizer=SGD, sync_bn=False, workers=8, project=runs/train, name=exp, exist_ok=False, quad=False, cos_lr=False, label_smoothing=0.0, patience=100, freeze=[0], save_period=-1, seed=0, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest, ndjson_console=False, ndjson_file=False
github: up to date with https://github.com/ultralytics/yolov5 ✅
YOLOv5 🚀 v7.0-368-gb163ff8d Python-3.10.14 torch-2.4.1+cu121 CUDA:0 (NVIDIA GeForce RTX 3060, 12036MiB)

hyperparameters: lr0=0.01, lrf=0.01, momentum=0.937, weight_decay=0.0005, warmup_epochs=3.0, warmup_momentum=0.8, warmup_bias_lr=0.1, box

### Test Inference

In [34]:
!python detect.py --weights runs/train/exp7/weights/best.pt --img 640 --conf 0.35 --source /home/aakash/Aakash/object_detection/thermal_images/test/video/thermal_test_video.mp4

detect: weights=['runs/train/exp7/weights/best.pt'], source=/home/aakash/Aakash/object_detection/thermal_images/test/video/thermal_test_video.mp4, data=data/coco128.yaml, imgsz=[640, 640], conf_thres=0.35, iou_thres=0.45, max_det=1000, device=, view_img=False, save_txt=False, save_format=0, save_csv=False, save_conf=False, save_crop=False, nosave=False, classes=None, agnostic_nms=False, augment=False, visualize=False, update=False, project=runs/detect, name=exp, exist_ok=False, line_thickness=3, hide_labels=False, hide_conf=False, half=False, dnn=False, vid_stride=1
YOLOv5 🚀 v7.0-368-gb163ff8d Python-3.10.14 torch-2.4.1+cu121 CUDA:0 (NVIDIA GeForce RTX 3060, 12036MiB)

Fusing layers... 
Model summary: 157 layers, 7050580 parameters, 0 gradients, 15.9 GFLOPs
video 1/1 (1/3749) /home/aakash/Aakash/object_detection/thermal_images/test/video/thermal_test_video.mp4: 512x640 1 person, 1 car, 24.5ms
video 1/1 (2/3749) /home/aakash/Aakash/object_detection/thermal_images/test/video/thermal_test

In [24]:
### converting the test images into video
import cv2
import os

# Path to the folder containing test images
images_folder = "/home/aakash/Aakash/object_detection/thermal_images/test/images"
# Output video file path
output_video = "/home/aakash/Aakash/object_detection/thermal_images/test/video/thermal_test_video.mp4"

# Get a list of all images in the folder, sorted by name (to maintain frame order)
images = sorted([img for img in os.listdir(images_folder) if img.endswith(('.jpg', '.png'))])

# Set video parameters
frame = cv2.imread(os.path.join(images_folder, images[0]))
height, width, layers = frame.shape

# Define the codec and create VideoWriter object
fourcc = cv2.VideoWriter_fourcc(*'mp4v')  # Codec for .mp4
video = cv2.VideoWriter(output_video, fourcc, 30, (width, height))

# Write each image to the video
for image in images:
    img_path = os.path.join(images_folder, image)
    frame = cv2.imread(img_path)
    video.write(frame)

# Release the video writer
video.release()

print(f"Video saved as {output_video}")


Video saved as /home/aakash/Aakash/object_detection/thermal_images/test/video/thermal_test_video.mp4


In [21]:
## Step 1
import json

# Path to the original coco.json
coco_json_path = "/home/aakash/Aakash/object_detection/task-4_thermal-object-detection/data/FLIR_ADAS_v2/video_thermal_test/coco.json"
# Path to save the updated coco.json
updated_coco_json_path = "/home/aakash/Aakash/object_detection/task-4_thermal-object-detection/data/FLIR_ADAS_v2/video_thermal_test/coco_updated.json"

# Load coco.json
with open(coco_json_path, 'r') as f:
    coco_data = json.load(f)

# Update file_name by removing the "data/" prefix
for image in coco_data['images']:
    image['file_name'] = image['file_name'].replace('data/', '')

# Save the updated coco.json
with open(updated_coco_json_path, 'w') as f:
    json.dump(coco_data, f)

print(f"Updated coco.json saved to {updated_coco_json_path}")


Updated coco.json saved to /home/aakash/Aakash/object_detection/task-4_thermal-object-detection/data/FLIR_ADAS_v2/video_thermal_test/coco_updated.json


### Step2. Run coco2yolo.py --> Update paths

In [22]:
## Step3 All images donot have images, create empty file for the images which donot have labels
import os

# Path to your images directory
images_dir = "/home/aakash/Aakash/object_detection/task-4_thermal-object-detection/data/FLIR_ADAS_v2/video_thermal_test/data"
# Path to your labels directory
labels_dir = "/home/aakash/Aakash/object_detection/task-4_thermal-object-detection/data/FLIR_ADAS_v2/video_thermal_test/labels"

# List of all images
image_files = [f for f in os.listdir(images_dir) if f.endswith(('.jpg', '.png'))]

# List of all labels
label_files = [f.replace('.txt', '') for f in os.listdir(labels_dir) if f.endswith('.txt')]

# Create empty label files for images without corresponding labels
missing_labels = 0
for image_file in image_files:
    image_name = os.path.splitext(image_file)[0]  # Get the image name without extension
    label_file_path = os.path.join(labels_dir, f"{image_name}.txt")
    
    # Check if the label exists, if not create an empty .txt file
    if image_name not in label_files:
        with open(label_file_path, 'w') as f:
            pass  # Create an empty file
        missing_labels += 1

print(f"Created {missing_labels} empty label files for images without annotations.")


Created 256 empty label files for images without annotations.


In [16]:
## other
import os

# Define the directory where label files are stored
labels_dir = "/home/aakash/Aakash/object_detection/thermal_images/train/labels"

# Define the number of classes
num_classes = 15

# Check each label file
for label_file in os.listdir(labels_dir):
    if label_file.endswith('.txt'):
        file_path = os.path.join(labels_dir, label_file)
        with open(file_path, 'r') as f:
            for line in f:
                class_id = int(line.split()[0])
                if class_id >= num_classes:
                    print(f"Invalid class {class_id} in file: {label_file}")


Invalid class 36 in file: video-JFiGa9oAAN2queuLt-frame-002697-Djrrde8jRkAfT746C.txt
Invalid class 36 in file: video-JFiGa9oAAN2queuLt-frame-002697-Djrrde8jRkAfT746C.txt
Invalid class 78 in file: video-DJYDQTZH7GLCqw3Tx-frame-004211-xaZTsKtZsxyyz6Ju8.txt
Invalid class 16 in file: video-7EPybiwBrzjDKn7TZ-frame-002127-9yW873ZwvdyDiFcy4.txt
Invalid class 78 in file: video-7EPybiwBrzjDKn7TZ-frame-004028-jGrhd6YyjSshnf2kh.txt
Invalid class 78 in file: video-7EPybiwBrzjDKn7TZ-frame-004028-jGrhd6YyjSshnf2kh.txt
Invalid class 78 in file: video-7EPybiwBrzjDKn7TZ-frame-004028-jGrhd6YyjSshnf2kh.txt
Invalid class 78 in file: video-GMDwNs5TdqejpF4vu-frame-000300-NXCr3TGo3C9gRmYpx.txt
Invalid class 78 in file: video-DJYDQTZH7GLCqw3Tx-frame-004291-sBa3CHFzA4eXvaZmm.txt
Invalid class 78 in file: video-SyzNY82LYZrhkPH7x-frame-000803-pdFn6fAFuTBJvstDR.txt
Invalid class 78 in file: video-DJYDQTZH7GLCqw3Tx-frame-003371-uWoxBFKu9Fcdf4eeJ.txt
Invalid class 78 in file: video-KTtJnXH7CcPgLeF2G-frame-002229-Lx

In [17]:
## Other
import os

# Path to the labels directory
labels_dir = "/home/aakash/Aakash/object_detection/thermal_images/train/labels"

# Maximum valid class ID
max_valid_class = 14

# Check and fix each label file
for label_file in os.listdir(labels_dir):
    if label_file.endswith('.txt'):
        label_file_path = os.path.join(labels_dir, label_file)
        updated_lines = []
        
        # Open the label file and process each line
        with open(label_file_path, 'r') as f:
            lines = f.readlines()
            for line in lines:
                class_id = int(line.split()[0])
                if class_id <= max_valid_class:
                    updated_lines.append(line)  # Keep valid lines only
        
        # Write back the valid lines, excluding the invalid ones
        with open(label_file_path, 'w') as f:
            f.writelines(updated_lines)

print("Invalid classes removed from label files.")


Invalid classes removed from label files.


In [19]:
## Other 
import os

# Path to the labels directory
labels_dir = "/home/aakash/Aakash/object_detection/thermal_images/val/labels"

# Maximum valid class ID
max_valid_class = 14

# Check and fix each label file
for label_file in os.listdir(labels_dir):
    if label_file.endswith('.txt'):
        label_file_path = os.path.join(labels_dir, label_file)
        updated_lines = []
        
        # Open the label file and process each line
        with open(label_file_path, 'r') as f:
            lines = f.readlines()
            for line in lines:
                class_id = int(line.split()[0])
                if class_id <= max_valid_class:
                    updated_lines.append(line)  # Keep valid lines only
        
        # Write back the valid lines, excluding the invalid ones
        with open(label_file_path, 'w') as f:
            f.writelines(updated_lines)

print("Invalid classes removed from label files.")


Invalid classes removed from label files.
